In [1]:
!git clone https://github.com/ultralytics/yolov5
%cd yolov5
%pip install -r requirements.txt

fatal: destination path 'yolov5' already exists and is not an empty directory.
/Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/yolov5


/Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/venv_training/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


  Using cached GitPython-3.1.44-py3-none-any.whl.metadata (13 kB)
  Using cached matplotlib-3.10.1-cp310-cp310-macosx_11_0_arm64.whl.metadata (11 kB)
  Using cached opencv_python-4.11.0.86-cp37-abi3-macosx_13_0_arm64.whl.metadata (20 kB)
  Using cached requests-2.32.3-py3-none-any.whl.metadata (4.6 kB)
  Using cached scipy-1.15.2-cp310-cp310-macosx_14_0_arm64.whl.metadata (61 kB)
  Using cached thop-0.1.1.post2209072238-py3-none-any.whl.metadata (2.7 kB)
  Using cached tqdm-4.67.1-py3-none-any.whl.metadata (57 kB)
  Using cached ultralytics-8.3.111-py3-none-any.whl.metadata (37 kB)
  Using cached pandas-2.2.3-cp310-cp310-macosx_11_0_arm64.whl.metadata (89 kB)
  Using cached seaborn-0.13.2-py3-none-any.whl.metadata (5.4 kB)
  Using cached gitdb-4.0.12-py3-none-any.whl.metadata (1.2 kB)
  Using cached contourpy-1.3.2-cp310-cp310-macosx_11_0_arm64.whl.metadata (5.5 kB)
  Using cached cycler-0.12.1-py3-none-any.whl.metadata (3.8 kB)
  Using cached fonttools-4.57.0-cp310-cp310-macosx_10_9_u

In [2]:
from PIL import Image
import os
import shutil
import random
import torch


In [3]:
orig_img_dir = "/Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/train/train_image"
orig_lbl_dir = "/Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/train/train_annotation"

yolo_images_dir = "/Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/yolov5/train/images"
yolo_labels_dir = "/Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/yolov5/train/labels"

In [4]:
os.makedirs(yolo_images_dir, exist_ok=True)
os.makedirs(yolo_labels_dir, exist_ok=True)

# Helper Functions

In [5]:
def convert_to_yolo_format(img_path, label_line):
    _, label, x1, y1, x2, y2 = label_line.strip().split()
    x1, y1, x2, y2 = map(int, (x1, y1, x2, y2))
    
    image = Image.open(img_path)
    w, h = image.size

    # Convert to YOLO format
    x_center = ((x1 + x2) / 2) / w
    y_center = ((y1 + y2) / 2) / h
    width = (x2 - x1) / w
    height = (y2 - y1) / h

    return f"0 {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f}"

In [6]:
converted = 0
skipped = 0

for file in os.listdir(orig_img_dir):
    if not file.endswith('.jpg'):
        continue

    img_path = os.path.join(orig_img_dir, file)
    lbl_path = os.path.join(orig_lbl_dir, file.replace('.jpg', '.txt'))

    if not os.path.exists(lbl_path):
        print(f"Missing label for {file}, skipping...")
        skipped += 1
        continue

    with open(lbl_path, 'r') as f:
        line = f.readline().strip()
        if not line:
            print(f"Empty label in {file}, skipping...")
            skipped += 1
            continue

    # Convert and save label
    yolo_label = convert_to_yolo_format(img_path, line)
    label_out_path = os.path.join(yolo_labels_dir, file.replace('.jpg', '.txt'))

    with open(label_out_path, 'w') as f:
        f.write(yolo_label + '\n')

    # Copy image
    shutil.copy(img_path, os.path.join(yolo_images_dir, file))
    converted += 1

print(f"Converted: {converted} | Skipped: {skipped}")

✅ Converted: 7109 | ❌ Skipped: 0


In [7]:
root = "/Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/"

In [8]:
# Base YOLO data folders
base_images = root+"yolov5/train/images"
base_labels = root+"yolov5/train/labels"

# New split folders
train_img_dir = root+"yolov5/train_split/images"
train_lbl_dir = root+"yolov5/train_split/labels"
val_img_dir = root+"yolov5/val_split/images"
val_lbl_dir = root+"yolov5/val_split/labels"

In [9]:
print(val_lbl_dir)

/Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/yolov5/val_split/labels


In [10]:
for folder in [train_img_dir, train_lbl_dir, val_img_dir, val_lbl_dir]:
    os.makedirs(folder, exist_ok=True)

In [11]:
all_images = [f for f in os.listdir(base_images) if f.endswith(".jpg")]
random.shuffle(all_images)
split_idx = int(0.8 * len(all_images))
train_files = all_images[:split_idx]
val_files = all_images[split_idx:]

def copy_split(files, src_img_dir, src_lbl_dir, dst_img_dir, dst_lbl_dir):
    for file in files:
        shutil.copy(os.path.join(src_img_dir, file), os.path.join(dst_img_dir, file))
        label_file = file.replace(".jpg", ".txt")
        shutil.copy(os.path.join(src_lbl_dir, label_file), os.path.join(dst_lbl_dir, label_file))
copy_split(train_files, base_images, base_labels, train_img_dir, train_lbl_dir)
copy_split(val_files, base_images, base_labels, val_img_dir, val_lbl_dir)

print(f"Train files: {len(train_files)}")
print(f"Val files: {len(val_files)}")

✅ Train files: 5687
✅ Val files: 1422


In [12]:
os.makedirs(root+"yolov5/data", exist_ok=True)

In [13]:
yaml_content = """
train: ../train_split/images
val: ../val_split/images

nc: 1
names: ['weapon']
"""

with open(root+"yolov5/data/opixray.yaml", "w") as f:
    f.write(yaml_content)

print("opixray.yaml created at yolov5/data/opixray.yaml")


✅ opixray.yaml created at yolov5/data/opixray.yaml


# Model Training To Run on Apple Silicon

In [14]:
#Made to utlilize mac hardware for training
!python train.py --img 416 --batch 16 --epochs 30 --data data/opixray.yaml --weights yolov5s.pt --name opixray_local --cache --device mps

train: weights=yolov5s.pt, cfg=, data=data/opixray.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=30, batch_size=16, imgsz=416, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, evolve_population=data/hyps, resume_evolve=None, bucket=, cache=ram, image_weights=False, device=mps, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=opixray_local, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=100, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest, ndjson_console=False, ndjson_file=False
github: skipping check (offline), for updates see https://github.com/ultralytics/yolov5
YOLOv5 🚀 v7.0-416-gfe1d4d99 Python-3.10.17 torch-2.8.0.dev20250420 MPS

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, c

In [15]:
model = torch.hub.load('ultralytics/yolov5', 'custom', path='runs/train/opixray_local4/weights/best.pt')
save_path = '/Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/trained_model.pt'
torch.save(model.state_dict(), save_path)
print(f"Trained model saved to: {save_path}")

/Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/venv_training/lib/python3.10/site-packages/torch/hub.py:330: UserWarning: You are about to download and run code from an untrusted repository. In a future release, this won't be allowed. To add the repository to your trusted list, change the command to {calling_fn}(..., trust_repo=False) and a command prompt will appear asking for an explicit confirmation of trust, or load(..., trust_repo=True), which will assume that the prompt is to be answered with 'yes'. You can also use load(..., trust_repo='check') which will only prompt for confirmation if the repo is not already trusted. This will eventually be the default behaviour
  warnings.warn(


Downloading: "https://github.com/ultralytics/yolov5/zipball/master" to /Users/manu/.cache/torch/hub/master.zip


YOLOv5 🚀 2025-4-20 Python-3.10.17 torch-2.8.0.dev20250420 CPU

Fusing layers... 
Model summary: 157 layers, 7012822 parameters, 0 gradients, 15.8 GFLOPs
Adding AutoShape... 


✅ Trained model saved to: /Users/manu/Documents/01_coursework_SJSU/Semester_2/255_datamining_cmpe255/project/trained_model.pt
